# Exploration 3

#### List of (more immediate) business questions:

* Q1. What are the top categories of products?
* Q2. For each category of product, what are the sub categories? E.g., Security software is a sub category of Software
* Q3. In each product category, what are all the brands ?
* Q4. How is rating stats (total reviews, average star rating, std deviations) for a given product, sub cat, brand
* Q5. How do these ratings change over time ?
* Q6. What are the span of dates reviews are submitted? Date range.
* Q7. Can we create an automatic rating system ? In: Comments/reviews in text -> Out: star rating: 1 to 5


#### My approach to this project:
* There are otherwise inclined automations due to its challenging nature and lack of time, are done for now manually but machine later 'NMLM' , a reference you will see from time to time in this project comments

In [2]:
# Answer to *** Q1 ***
product_categories=["Apparel", "Automotive", "Baby","Beauty","Books","Camera","Ebook","Music","Software",
"Digital_Video","Digital_Video_Games","Electronics","Furniture","Gift_Card","Grocery","Health_Personal_Care",
"Home_Entertainment","Home_Improvement","Home","Jewelry","Kitchen","Lawn_and_Garden","Luggage",
"Major_Appliances","Mobile_Apps","Mobile_Electronics","Music","Musical_Instruments","Office_Products","Outdoors","PC",
"Personal_Care_Appliances","Pet_Products","Shoes", "Software","Sports","Tools","Toys","Video_DVD","Video_Games",
"Video", "Watches", "Wireless"]

In [1]:
# This is to prepare environment and import libraries
%matplotlib inline
import numpy as np
import pandas as pd
from pylab import *
import matplotlib
import matplotlib.pyplot as plt
import os
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import PunktSentenceTokenizer
import random
import pickle

In [3]:
brands={}
product_trademarks={}
questionables = {}
# Software brands, obtained for now manually, machine later NMLM from http://www.softwaremedia.com/credentials

# TODO: need also to handle equivalent class , e.g., Norton is a subgroup of Symantec

brands['software']=["Acronis", "Adobe", "Apache", "ArcSoft", "Autodesk", "Avast", "AVG", "BitDefender", "Borland", 
    "Business Objects", "CA", "Connectify ", "Corel", "DeLorme", "Enfocus", "ESET", "FileMaker", "H&R Block", "IGG", 
    "Infinite Skills", "Insperity", "Intuit", "Kaspersky", "Laplink","Mac", "Magix", "MakerBot", "McAfee", "McGraw-Hill", 
    "Microsoft", "Microsoft Surface", "Nero", "Norton", "Nuance", "Parallels", "PC Matic", "Piriform", "Punch", "Quark", 
    "QuickBooks", "Quicken", "Roxio", "Sage", "SoftwareMedia", "Sony", "StorageCraft", "Symantec", "Techsmith", 
    "Thomson Reuters", "Trend Micro", "V7", "Veeam", "VMware", "Webroot" ]

product_trademarks['software']=['Turbotax', "Ccleaner", "Amazon Drive", "Amazon Drive Desktop", "Banktivity", "Fotor", 
    "LearnSmart", "Malwarebytes", "Mavis Beacon", "Merriam Webster", "Office", "PCMover", "Photoshop", "ResumeMaker",
    "SecureAnywhere", "Simplitude", "Street Atlas", "TaxAct", "Toast 11 Titanium"]

questionables['software']=['psBackup']

In [4]:
#raw_reviews=pd.read_csv('data/raw/amazon_reviews_us_Software_v1_00.tsv',delimiter='\t', encoding='latin-1')
raw_reviews=pd.read_csv('data/raw/amazon_reviews_us_Digital_Software_v1_00.tsv',delimiter='\t', encoding='latin-1')

In [54]:
#len(raw_reviews)  # 101836

In [55]:
# Pare the size way down for prototyping
#raw_reviews=raw_reviews[:20000].copy()

In [16]:
raw_reviews[:3]

customer_id       review_id  product_id  \
0     17747349  R2EI7QLPK4LF7U  B00U7LCE6A   
1     10956619  R1W5OMFK1Q3I3O  B00HRJMOM4   
2     13132245   RPZWSYWRP92GI  B00P31G9PQ   

                        product_title  product_category  star_rating  \
0            CCleaner Free [Download]  Digital_Software            4   
1  ResumeMaker Professional Deluxe 18  Digital_Software            3   
2           Amazon Drive Desktop [PC]  Digital_Software            1   

  review_headline                    review_body review_date sentiment  \
0      Four Stars                 So far so good  2015-08-31  Positive   
1     Three Stars  Needs a little more work.....  2015-08-31   Neutral   
2        One Star                 Please cancel.  2015-08-31  Negative   

                   tags  length  
0              ccleaner      14  
1           resumemaker      29  
2  amazon drive desktop      14

In [5]:
categorical=raw_reviews.dtypes[raw_reviews.dtypes=="object"].index
raw_reviews[categorical].describe()

marketplace       review_id  product_id  \
count       101836          101836      101836   
unique           1          101836        2995   
top             US  R2B5OXJVXTAFGO  B00H9A60O4   
freq        101836               1        9462   

                               product_title  product_category    vine  \
count                                 101836            101836  101836   
unique                                  2639                 1       1   
top     Avast Free Antivirus 2015 [Download]  Digital_Software       N   
freq                                    9462            101836  101836   

       verified_purchase review_headline review_body review_date  
count             101836          101836      101836      101831  
unique                 2           69680       98421        2198  
top                    Y      Five Stars       Great  2015-03-04  
freq               70682            8904         131         445

In [6]:
# Related to *** Q6 ***
#   For Software, the earliest is 1998-09-21, the last reviews were on 2015-08-31
raw_reviews["review_date"].sort_values().unique()

array(['2008-01-26', '2008-02-05', '2008-02-08', ..., '2015-08-30',
       '2015-08-31', nan], dtype=object)

In [7]:
# To simplify the investigation, dropping the unused (for now) fields
raw_reviews=raw_reviews.drop(['marketplace','product_parent','helpful_votes','total_votes','vine','verified_purchase'], axis=1)

In [8]:
# Add sentiment column to the dataframe based on star_rating 
raw_reviews['sentiment'] = raw_reviews.star_rating.map({1:'Negative', 2:'Negative', 3:'Neutral', 4:'Positive', 5:'Positive'})

In [9]:
raw_reviews['tags']=""
raw_reviews['length']=0

In [12]:
categorical=raw_reviews.dtypes[raw_reviews.dtypes=="object"].index
raw_reviews[categorical].describe()

review_id  product_id                         product_title  \
count           101836      101836                                101836   
unique          101836        2995                                  2639   
top     R2B5OXJVXTAFGO  B00H9A60O4  Avast Free Antivirus 2015 [Download]   
freq                 1        9462                                  9462   

        product_category review_headline review_body review_date sentiment  \
count             101836          101836      101836      101831    101836   
unique                 1           69680       98421        2198         3   
top     Digital_Software      Five Stars       Great  2015-03-04  Positive   
freq              101836            8904         131         445     62957   

          tags  
count   101836  
unique       1  
top             
freq    101836

In [66]:
#for idx, row in df.iterrows():
#    if  df.loc[idx,'Qty'] == 1 and df.loc[idx,'Price'] == 10:
#        df.loc[idx,'Buy'] = 1
        
###### Useful syntax ######
#for index, r in raw_reviews.iterrows():
#    if index == 2:
#        raw_reviews.at[index, 'tags'] = (2,1)
    #print(r['tags'])

    

In [13]:
#####
# Preprocessing: tagging each review with brands, or product trademarks, to facilitate filtering and search
#####

from fuzzywuzzy import fuzz, process
something_count=0
nothing_count=0
potential_names = brands['software'] + product_trademarks['software']

for index, row in raw_reviews.iterrows():
    #print("Title: ", t)
    t = row['product_title']
    print(t)
    #results = process.extract(t, brands['software'], limit=3)
    #results2 = process.extract(t, product_trademarks['software'], limit=3)
    #print(results + results2)
    #combined_results = results + results2
    combined_results = process.extract(t, potential_names, limit=3)
    qualified=[]
    # Use 59% as confidence and inclusion level
    for r in (combined_results): 
        if r[1] > 59:
            qualified.append(r)
    
    # Populate frame with comment length
    raw_reviews.at[index, 'length'] = len(row['review_body'])

    # Populate frame with tag(s) if qualified ones found
    tags_to_insert = ""
    if len(qualified)>0:
        #print("Qualified: ", qualified)
        something_count+=1
        #print(qualified[0][0])
        tags_to_insert = qualified[0][0]
        
        # If the 2nd place is less than 4% behind the 1st place, include the 2nd place name too as tags
        try: 
            if (qualified[0][1] - qualified[1][1] < 4):
                tags_to_insert = tags_to_insert + "|" + qualified[1][0]
        except(IndexError): # Ok to by pass this one when there's only one item qualified
            pass
        
        tags_to_insert = tags_to_insert.lower()
        print("Tags to insert: ", tags_to_insert)
        raw_reviews.at[index, 'tags'] = tags_to_insert
        #print("Tags to Insert: ", tags_to_insert)
    else:
        #print("Title: ", t)
        #print("NOTHING")
        #print("Combined results: ", combined_results)
        nothing_count+=1
        
print("Nothing count: ", nothing_count)
print("Something count: ", something_count)


CCleaner Free [Download]
Tags to insert:  ccleaner
ResumeMaker Professional Deluxe 18
Tags to insert:  resumemaker
Amazon Drive Desktop [PC]
Tags to insert:  amazon drive desktop
Norton Internet Security 1 User 3 Licenses
Tags to insert:  norton
SecureAnywhere Intermet Security Complete 5 Device
Tags to insert:  secureanywhere
Pc Matic Performance Utility Suite (5 User Edition)
Tags to insert:  pc matic
Microsoft OneNote 2013 (1PC/1User)
Tags to insert:  microsoft
Intuit Quicken Rental Property Manager 2015
Tags to insert:  intuit|quicken
Avast Free Antivirus 2015 [Download]
Tags to insert:  avast
Apache OpenOffice 3.4.1
Tags to insert:  apache|office
Norton Security
Tags to insert:  norton
Corel Painter Essentials 5 For Mac And Windows
Tags to insert:  corel|mac
Norton Security with Back Up
Tags to insert:  norton
Movavi Screen Capture 5 Personal Edition [Download]
Tags to insert:  ca
Photoshop Elements & Premiere Elements 13
Tags to insert:  photoshop
LearnSmart for The Art of Public

Tags to insert:  learnsmart
Microsoft Outlook 2013 (1PC/1User)
Tags to insert:  microsoft
Arithmemouse Addition Subtraction Free [Download]
Tags to insert:  taxact
PaperPort Professional 14
Tags to insert:  nero
Quicken Deluxe 2013
Tags to insert:  quicken
Kaspersky Internet Security 2015 3 User, 1 Year
Tags to insert:  kaspersky
Block Financial H&R Block Tax Software 14 Deluxe + State
Tags to insert:  h&r block
Pc Matic Performance Utility Suite (5 User Edition)
Tags to insert:  pc matic
Movavi Video Suite 12 Video Editing Software Personal [Download]
Tags to insert:  softwaremedia
Norton Security
Tags to insert:  norton
Pc Matic Performance Utility Suite (5 User Edition)
Tags to insert:  pc matic
Norton Security
Tags to insert:  norton
Kaspersky Anti-Virus 2015 3 User, 1 Year
Tags to insert:  kaspersky
Intuit Quicken Home & Business 2015
Tags to insert:  intuit|quicken
Norton Security with Back Up
Tags to insert:  norton
Corel CorelDRAW Home and Student Suite X7
Tags to insert:  core

TaxACTÂ® 2014 Free Federal Edition [Download]
Tags to insert:  taxact
Photoshop Elements 13
Tags to insert:  photoshop
WordPerfect Office X7 Home and Student
Tags to insert:  office
Photoshop Elements & Premiere Elements 13 - Student and Teacher Edition
Tags to insert:  photoshop
Kaspersky Pure 3.0 Total Security
Tags to insert:  kaspersky
Microsoft Retail Office Home Business 2013 Product Key
Tags to insert:  microsoft
Block Financial H&R Block Tax Software 14 Deluxe + State
Tags to insert:  h&r block
Sound Forge
Tags to insert:  sony
Microsoft Office Home and Student 2013 (1PC/1User) [Download]
Tags to insert:  microsoft
Xara Photo & Graphic Designer 9 - Free Trial [Download]
Norton Security with Back Up
Tags to insert:  norton
Apache OpenOffice 3.4.1
Tags to insert:  apache|office
Adobe Acrobat XI Standard
Tags to insert:  adobe
Norton Security with Back Up
Tags to insert:  norton
Avast Free Antivirus 2015 [Download]
Tags to insert:  avast
Microsoft 8.1 Upgrade
Tags to insert:  micr

Tags to insert:  toast 11 titanium
Laplink PCmover Professional 8 - 1 Use [Download]
Tags to insert:  laplink|pcmover
Norton Security with Back Up
Tags to insert:  norton
LearnSmart for Psychsmart
Tags to insert:  learnsmart
IObit Uninstaller 4 [Download]
Tags to insert:  intuit
Norton Security (For 5 Devices) for Students [Online Code]
Tags to insert:  insperity|norton
Kaspersky Anti-Virus 2015 3 User, 1 Year
Tags to insert:  kaspersky
Quicken Deluxe Personal Finance & Budgeting Software 2015
Tags to insert:  quicken
Cook'n Recipe Organizer Version 11 MAC [Download]
Tags to insert:  toast 11 titanium
QuickBooks Pro with Enhanced Payroll 2015
Tags to insert:  quickbooks
LibreOffice v4.3
Tags to insert:  office
Microsoft Office 365 Personal 1yr Subscription
Tags to insert:  microsoft|office
Adobe Photoshop Lightroom 5 Student and Teacher Edition
Tags to insert:  photoshop
Dragon NaturallySpeaking Home 13.0
Norton Security
Tags to insert:  norton
Quicken Deluxe Personal Finance & Budgeti

Tags to insert:  microsoft
Kaspersky Internet Security 2015 3 User, 1 Year
Tags to insert:  kaspersky
Excel Budget Software and Checkbook Register Spreadsheet Template - Free Trial Version - Requires Microsoft Excel 2007, Excel 2010, Excel 2013 or higher [Download]
Tags to insert:  microsoft
Bitdefender Total Security 2015 - up to 3 PCs, 1 year [Download]
Tags to insert:  bitdefender
Norton Security
Tags to insert:  norton
Norton Security
Tags to insert:  norton
Bitdefender Antivirus Plus 2013 (3PC/1YR) [Download]
Tags to insert:  bitdefender
Microsoft Retail Office Home Business 2013 Product Key
Tags to insert:  microsoft
Cook'n Recipe Organizer Version 11 PC [Download]
Tags to insert:  pc matic|toast 11 titanium
SecureAnywhere Intermet Security Complete 5 Device
Tags to insert:  secureanywhere
Corel PaintShop Pro X7
Tags to insert:  corel
H&R Block At Home 2013 Deluxe + State
Tags to insert:  h&r block
TurboTax Deluxe Fed + Efile
Tags to insert:  turbotax
Quicken WillMaker Plus 2015


...

Tags to insert:  quicken
QuickBooks Pro 2010
Tags to insert:  quickbooks
TurboTax Deluxe Federal + efile 2009
Tags to insert:  turbotax
H&R Block At Home 2009 Basic Federal + eFile [Formerly TaxCut]
Tags to insert:  h&r block
H&R Block At Home 2009 Premium & Business Federal + State + eFile
Tags to insert:  h&r block
H&R Block At Home 2009 Premium Federal + State + eFile
Tags to insert:  h&r block
Quicken Home & Business 2010
Tags to insert:  quicken
Quicken Starter Edition 2009
Tags to insert:  quicken
Quicken Deluxe 2010 [OLD VERSION]
Tags to insert:  quicken
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
TurboTax Business Federal + efile 2009
Tags to insert:  turbotax
AVG Internet Security 3 User - 2 Year Subscription
Tags to insert:  avg
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
H&R Block At Home 2009 Deluxe Federal + eFile
Tags to insert:  h&r block
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags t

Tags to insert:  quicken
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
TurboTax Deluxe Federal + eFile + State 2009
Tags to insert:  turbotax
TurboTax Deluxe Federal + eFile + State 2009
Tags to insert:  turbotax
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
Garmin nuMaps Lifetime North America Map Updates
Tags to insert:  ca|norton
Quicken Premier 2010
Tags to insert:  quicken
TurboTax Deluxe Federal + eFile + State 2009
Tags to insert:  turbotax
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
TurboTax Deluxe Federal + eFile + State 2009
Tags to insert:  turbotax
TurboTax Deluxe Federal + efile 2009
Tags to insert:  turbotax
TurboTax Home & Busi

Tags to insert:  quicken
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
TurboTax Deluxe Federal + eFile + State 2009
Tags to insert:  turbotax
QuickBooks Pro 2010
Tags to insert:  quickbooks
TurboTax Deluxe Federal + State + eFile 2008
Tags to insert:  turbotax
TurboTax Home & Business Federal + State + Federal efile 2009
Tags to insert:  turbotax
Quicken Deluxe 2010 [OLD VERSION]
Tags to insert:  quicken
Quicken Starter Edition 2010
Tags to insert:  quicken
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
TurboTax Home & Business Federal + State + Federal efile 2009
Tags to insert:  turbotax
H&R Block At Home 2009 Deluxe Federal + State + eFile
Tags to insert:  h&r block
TurboTax Premier Federal + State + Federal efile 2009
Tags to insert:  turbotax
QuickBooks Pro 2010
Tags to insert:  quickbooks
H&R Block At Home 2009 Premium & Business Federal + State + eFile
Tags to insert:  h&r block
TurboTax Deluxe Federal + eFile 

Tags to insert:  quicken
QuickBooks Pro 2009
Tags to insert:  quickbooks
Intuit Quicken Deluxe 2009
Tags to insert:  intuit|quicken
Intuit Quicken Deluxe 2009
Tags to insert:  intuit|quicken
Intuit Quicken Deluxe 2009
Tags to insert:  intuit|quicken
Better Homes and Gardens Architectural Home Designer
Quicken Premier 2009
Tags to insert:  quicken
QuickBooks Pro 2009
Tags to insert:  quickbooks
Intuit Quicken Deluxe 2009
Tags to insert:  intuit|quicken
Better Homes and Gardens Landscaping and Deck Designer 8.0
Tags to insert:  ca
Quicken Starter Edition 2009
Tags to insert:  quicken
Intuit Quicken Deluxe 2009
Tags to insert:  intuit|quicken
Intuit Quicken Deluxe 2009
Tags to insert:  intuit|quicken
Intuit Quicken Deluxe 2009
Tags to insert:  intuit|quicken
Better Homes and Gardens Home Designer Pro 8.0  [Download] [OLD VERSION]
Quicken Home & Business 2009
Tags to insert:  quicken
Quicken Starter Edition 2009
Tags to insert:  quicken
Quicken Home & Business 2009
Tags to insert:  quicken

Tags to insert:  h&r block
H&R Block TaxCut 2008 Home & Business + e-file
Tags to insert:  h&r block
TurboTax Deluxe Federal + State + eFile 2008
Tags to insert:  turbotax
TurboTax Home & Business Federal + State + eFile 2008 (Old Version) [DOWNLOAD]
Tags to insert:  business objects
TurboTax Deluxe Federal + State + eFile 2008
Tags to insert:  turbotax
H&R Block TaxCut 2008 Premium Federal + e-file
Tags to insert:  h&r block
TurboTax Deluxe Federal + State + eFile 2008
Tags to insert:  turbotax
TurboTax Deluxe Federal + State + eFile 2008
Tags to insert:  turbotax
H&R Block TaxCut 2008 Premium Federal + State + e-file
Tags to insert:  h&r block
H&R Block TaxCut 2008 Premium Federal + e-file
Tags to insert:  h&r block
TurboTax Deluxe Federal + State + eFile 2008
Tags to insert:  turbotax
H&R Block TaxCut 2008 Premium Federal + State + e-file
Tags to insert:  h&r block
TurboTax Deluxe Federal + State + eFile 2008
Tags to insert:  turbotax
TurboTax Deluxe Federal + State + eFile 2008
Tag

In [14]:
save_tagged_reviews = open("taggedDigitSoftwareReviews", "wb")
pickle.dump(raw_reviews, save_tagged_reviews)
save_tagged_reviews.close()